In [ ]:
# https://www.kaggle.com/shivamb/netflix-shows/tasks?taskId=2447

In [ ]:
# calculate matching score for content-based filtering with cosine similarity 
#  there would be three recommender
# - 1. recommend_genre(title)
#    : TF-IDF(listed_in) & one-hot(country) & categorical (without cast)
# - 2. recommend_description(title)
#    : one-hot TF(description, country) & categorical(type, rating) (without cast) 
# - 3. recommend_cast_country(title)
#    : one-hot encoding(cast, country) & categorical(type, rating)

In [1]:
# ---- <import library> ----
import numpy as np
import pandas as pd

from math import log
import re

import nltk
# nltk.download('punkt')
# nltk.download('averaged_perceptron_tagger')

# for cosine similarity
from numpy import dot
from numpy.linalg import norm
def cos_sim(A, B):
       return dot(A, B)/(norm(A)*norm(B))

pd.set_option("display.max_columns",None)

In [2]:
# ---- <read dataset> ----
df = pd.read_csv("../input/netflix-shows/netflix_titles.csv"")

In [3]:
# ---- <data cleansing> ----
# we need columns below. 
# [type, title, cast, country, rating, listed_in, description]

# delete unnecessary columns
df1 = df.copy()
df1.drop(columns=['show_id','date_added','release_year','director'],axis=1, inplace=True)

# handle with null data
df1.isnull().sum()

dfv1 = df1.copy()
ncol=['cast','country','rating']
values = {'cast': 'nodata', 'country': 'nodata', 'rating': 'nodata'}
dfv1.fillna(value=values,inplace=True)


In [4]:
# ------ < NLP and cosine similarity > ------
# A. convert to numerical 
# A.1. TF-IDF :  listed_in
# what is TF-IDF:  https://en.wikipedia.org/wiki/Tf–idf

# A.2. one-hot-encoding with TF: description, cast, country
# A.3. categorical: type, rating

# B. get cosine similarity
# B.1 TF-IDF(listed_in) & one-hot(country) & categorical
# B.2 TF-IDF(description) & one-hot(country) & categorical
# B.3 one-hot encoding & categorical


In [5]:
# A.1 TF-IDF 
# listed_in

# exclude word 'Movies', 'TV' because we have type field 
# generage new columns for tf-idf
exclude_wd = set(['movies','tv','&'])
f = lambda x: ' '.join(w for w in x.split() if not w in exclude_wd)
# generate new column 'genre'
dfv1['genre'] = dfv1['listed_in'].str.lower().replace(',','',regex=True)
dfv1['genre'] = dfv1['genre'].apply(f)

# count per term of genre
# each index would be the order of titles
def tf(t, d):
    return d.count(t)
arr_g = dfv1['genre']
voc_g = sorted(list(set(w for i in arr_g for w in i.split())))

voc_g_count = []
for i in range(len(arr_g)): 
    voc_g_count.append([])
    d = arr_g[i]
    for j in range(len(voc_g)):
        t = voc_g[j]        
        voc_g_count[-1].append(tf(t, d))

tf_g = pd.DataFrame(voc_g_count, columns = voc_g)
print('term count')
display(tf_g.head(5))

# tf-idf: how important the word is to a document(per each title)
# it doesn't recognize '-' as word, so 'sci-fi' would be splited into 'sci' and 'fi'
# each index would be the order of titles
from sklearn.feature_extraction.text import TfidfVectorizer
tfidfv_g = TfidfVectorizer().fit(arr_g)
tfidfv_g_r = tfidfv_g.transform(arr_g).toarray() # get tf-idf
# get each word list
tfidfv_g_v = sorted(tfidfv_g.vocabulary_.items(), key=lambda x: x[1]) 
voc_gt = []
for i in tfidfv_g_v:
    voc_gt.append(i[0])
# get dataframe with tf-idf
tfidfv_g_df = pd.DataFrame(tfidfv_g_r , columns = voc_gt)
# tfidfv_g_df = tfidfv_g_df.reindex(sorted(tfidfv_g_df.columns), axis=1)
print('tf-idf')
display(tfidfv_g_df.head(5))

term count


action  adventure  anime  british  children  classic  comedies  comedy  \
0       0          0      0        0         0        0         0       0   
1       0          0      0        0         0        0         0       0   
2       0          0      0        0         0        0         0       0   
3       1          1      0        0         0        0         0       0   
4       0          0      0        0         0        0         0       0   

   crime  cult  documentaries  docuseries  dramas  faith  family  fantasy  \
0      0     0              0           0       1      0       0        1   
1      0     0              0           0       1      0       0        0   
2      0     0              0           0       0      0       0        0   
3      0     0              0           0       0      0       0        1   
4      0     0              0           0       1      0       0        0   

   features  horror  independent  international  kids'  korean  lgbtq  music  \
0         0       0            0              1      0       0      0      0   
1         0       0            0              1      0       0      0      0   
2         0       1            0              1      0       0      0      0   
3         0       0            1              0      0       0      0      0   
4         0       0            0              0      0       0      0      0   

   musicals  mysteries  nature  reality  romantic  sci-fi  science  series  \
0         0          0       0        0         0       1        0       0   
1         0          0       0        0         0       0        0       0   
2         0          0       0        0         0       0        0       0   
3         0          0       0        0         0       1        0       0   
4         0          0       0        0         0       0        0       0   

   shows  spanish-language  spirituality  sports  stand-up  talk  teen  \
0      1                 0             0       0         0     0     0   
1      0                 0             0       0         0     0     0   
2      0                 0             0       0         0     0     0   
3      0                 0             0       0         0     0     0   
4      0                 0             0       0         0     0     0   

   thrillers  
0          0  
1          0  
2          0  
3          0  
4          0

tf-idf


action  adventure  anime  british  children  classic  comedies  comedy  \
0  0.000000   0.000000    0.0      0.0       0.0      0.0       0.0     0.0   
1  0.000000   0.000000    0.0      0.0       0.0      0.0       0.0     0.0   
2  0.000000   0.000000    0.0      0.0       0.0      0.0       0.0     0.0   
3  0.341928   0.341928    0.0      0.0       0.0      0.0       0.0     0.0   
4  0.000000   0.000000    0.0      0.0       0.0      0.0       0.0     0.0   

   crime  cult  documentaries  docuseries    dramas  faith  family   fantasy  \
0    0.0   0.0            0.0         0.0  0.243763    0.0     0.0  0.515932   
1    0.0   0.0            0.0         0.0  0.753545    0.0     0.0  0.000000   
2    0.0   0.0            0.0         0.0  0.000000    0.0     0.0  0.000000   
3    0.0   0.0            0.0         0.0  0.000000    0.0     0.0  0.458116   
4    0.0   0.0            0.0         0.0  1.000000    0.0     0.0  0.000000   

   features        fi    horror  independent  international  kids  korean  \
0       0.0  0.515932  0.000000     0.000000       0.212660   0.0     0.0   
1       0.0  0.000000  0.000000     0.000000       0.657397   0.0     0.0   
2       0.0  0.000000  0.915747     0.000000       0.401756   0.0     0.0   
3       0.0  0.458116  0.000000     0.369539       0.000000   0.0     0.0   
4       0.0  0.000000  0.000000     0.000000       0.000000   0.0     0.0   

   language  lgbtq  music  musicals  mysteries  nature  reality  romantic  \
0       0.0    0.0    0.0       0.0        0.0     0.0      0.0       0.0   
1       0.0    0.0    0.0       0.0        0.0     0.0      0.0       0.0   
2       0.0    0.0    0.0       0.0        0.0     0.0      0.0       0.0   
3       0.0    0.0    0.0       0.0        0.0     0.0      0.0       0.0   
4       0.0    0.0    0.0       0.0        0.0     0.0      0.0       0.0   

        sci  science  series     shows  spanish  spirituality  sports  stand  \
0  0.515932      0.0     0.0  0.311123      0.0           0.0     0.0    0.0   
1  0.000000      0.0     0.0  0.000000      0.0           0.0     0.0    0.0   
2  0.000000      0.0     0.0  0.000000      0.0           0.0     0.0    0.0   
3  0.458116      0.0     0.0  0.000000      0.0           0.0     0.0    0.0   
4  0.000000      0.0     0.0  0.000000      0.0           0.0     0.0    0.0   

   talk  teen  thrillers   up  
0   0.0   0.0        0.0  0.0  
1   0.0   0.0        0.0  0.0  
2   0.0   0.0        0.0  0.0  
3   0.0   0.0        0.0  0.0  
4   0.0   0.0        0.0  0.0

In [11]:
# A.2. one-hot-encoding with TF: description, cast, country
# 1) description
# too many description so extract only NOUN(NN)
# but too many time spent

import nltk
arr_d = dfv1['description']

voc_d = []
for text in arr_d:
    term = nltk.word_tokenize(text)
    qu = nltk.pos_tag(term)
    for e in qu:
        if e[1]=='NN':
            voc_d.append(e[0])
            
voc_ds=list(set(voc_d))

# tf
voc_d_count = []
for i in range(len(arr_d)): 
    voc_d_count.append([])
    d = arr_d[i]
    for j in range(len(voc_ds)):
        t = voc_ds[j]        
        voc_d_count[-1].append(tf(t, d))

tf_d = pd.DataFrame(voc_d_count, columns = voc_ds)
print('term count')
display(tf_d.head(5))

term count


debut  junkyard  Yijuan  quarry  propaganda  boomer  clown  break  \
0      0         0       0       0           0       0      0      0   
1      0         0       0       0           0       0      0      0   
2      0         0       0       0           0       0      0      0   
3      0         0       0       0           0       0      0      0   
4      0         0       0       0           0       0      0      0   

   conglomerate  autobiography  prank  casino  vistas  curmudgeon  cabdriver  \
0             0              0      0       0       0           0          0   
1             0              0      0       0       0           0          0   
2             0              0      0       0       0           0          0   
3             0              0      0       0       0           0          0   
4             0              0      0       1       0           0          0   

   programmer  orcas  go-to-guy  stride  cage  vulnerability  gem  gladiator  \
0           0      0          0       0     0              0    0          0   
1           0      0          0       0     0              0    0          0   
2           0      0          0       0     0              0    0          0   
3           0      0          0       0     0              0    0          0   
4           0      0          0       0     0              0    0          0   

   Zixin  hamster  lock  rec  skin  noblewoman  artist  threat  democracy  \
0      0        0     0    0     0           0       0       0          0   
1      0        0     0    0     0           0       0       0          0   
2      0        0     0    1     0           0       0       0          0   
3      0        0     0    0     0           0       0       0          0   
4      0        0     0    0     0           0       0       0          0   

   has-been  midnight  staff  cartoonist  packed  tech  activist  impression  \
0         0         0      0           0       0     0         0           0   
1         0         0      0           0       0     0         0           0   
2         0         0      0           0       0     0         0           0   
3         0         0      0           0       0     0         0           0   
4         0         0      0           0       0     0         0           0   

   indecisiveness  fairness  winner  gangland  tip  missing  harm  \
0               0         0       0         0    0        0     0   
1               0         0       0         0    0        0     0   
2               0         0       0         0    0        0     0   
3               0         0       0         0    0        0     0   
4               0         0       0         0    0        0     0   

   Manipulation  shaken  bungalow  supervisor  absence  outrage  await  \
0             0       0         0           0        0        0      0   
1             0       0         0           0        0        0      0   
2             0       0         0           0        0        0      0   
3             0       0         0           0        0        0      0   
4             0       0         0           0        0        0      0   

   kitchen  shipment  pigeon  bride-to-be  protection  deceit  Life  reishi  \
0        0         0       0            0           0       0     0       0   
1        0         0       0            0           0       0     0       0   
2        0         0       0            0           0       0     0       0   
3        0         0       0            0           0       0     0       0   
4        0         0       0            0           0       0     0       0   

   desert  Nate  cleansing  feud  drumming  orc  rapist  reincarnation  \
0       0     0          0     0         0    0       0              0   
1       0     0          0     0         0    0       0              0   
2       0     0          0     0         0    1       0              0   
3       0     0          0     0 

In [12]:
# 2) cast ; too many cast so catch only first cast
first_cast = []
for i in dfv1['cast']:
    a = i.split(',')[0]
    first_cast.append(a)
    
voc_cast=list(set(first_cast))
arr_c = dfv1['cast']

voc_c_count = []
for i in range(len(arr_c)): 
    voc_c_count.append([])
    d = arr_c[i]
    for j in range(len(voc_cast)):
        t = voc_cast[j]        
        voc_c_count[-1].append(tf(t, d))

tf_c = pd.DataFrame(voc_c_count, columns = voc_cast)
print("first cast count")
display(tf_c.head())

first cast count


Fiona Dourif  Neal Brennan  Robert Więckiewicz  Gerard Butler  \
0             0             0                   0              0   
1             0             0                   0              0   
2             0             0                   0              0   
3             0             0                   0              0   
4             0             0                   0              0   

   Subbu Talabi  Amber Kuo  Judy Davis  Michael Jordan  Saad El Soghayar  \
0             0          0           0               0                 0   
1             0          0           0               0                 0   
2             0          0           0               0                 0   
3             0          0           0               0                 0   
4             0          0           0               0                 0   

   Jacqueline Kim  Emre Karayel  Riley Wang  David Hasselhoff  Felicia Day  \
0               0             0           0                 0            0   
1               0             0           0                 0            0   
2               0             0           0                 0            0   
3               0             0           0                 0            0   
4               0             0           0                 0            0   

   Inthira Charoenpura  Riddhi Sen  Randy Wayne  Sidse Babett Knudsen  \
0                    0           0            0                     0   
1                    0           0            0                     0   
2                    0           0            0                     0   
3                    0           0            0                     0   
4                    0           0            0                     0   

   Maciej Musiałowski  Wu Kang-jen  Rahul Bairagi  Olasupo Shasore  \
0                   0            0              0                0   
1                   0            0              0                0   
2                   0            0              0                0   
3                   0            0              0                0   
4                   0            0              0                0   

   Yvan Attal  Nayantara  Siddharth Koirala  Nicholas Braun  \
0           0          0                  0               0   
1           0          0                  0               0   
2           0          0                  0               0   
3           0          0                  0               0   
4           0          0                  0               0   

   Johnathon Schaech  Fawad Khan  Parvathy Ratheesh  Joel Gretsch  Jim Henson  \
0                  0           0                  0             0           0   
1                  0           0                  0             0           0   
2                  0           0                  0             0           0   
3                  0           0                  0             0           0   
4                  0           0                  0             0           0   

   Travis Scott  Eugenio Derbez  Stefanie Scott  Leslie Jones  Carla Gugino  \
0             0               0               0             0             0   
1             0               0               0             0             0   
2             0               0               0             0             0   
3             0               0               0             0             0   
4             0               0               0             0             0   

   Ralph Macchio  Garth Brooks  Trevante Rhodes  Nour Al Ghandour  \
0              0             0                0                 0   
1              0             0                0                 0   
2              0             0                0                 0   
3              0             0                0                 0   
4              0             0                0                 0   

   David Sampliner  Warren Bullock  Kendall Schmidt 

In [13]:
# 3) country; catch only first country
first_cnt = []
for i in dfv1['country']:
    a = i.split(',')[0]
    first_cnt.append(a)

voc_cnt=list(set(first_cnt))
arr_ct = dfv1['country']

voc_ct = []
for i in range(len(arr_ct)): 
    voc_ct.append([])
    d = arr_ct[i]
    for j in range(len(voc_cnt)):
        t = voc_cnt[j]        
        voc_ct[-1].append(tf(t, d))

tf_ct = pd.DataFrame(voc_ct, columns = voc_cnt)
print('first country count')
display(tf_ct.head())

first country count


Saudi Arabia  Somalia  Hong Kong  Egypt  Austria  Netherlands  \
0             0        0          0      0        0            0   
1             0        0          0      0        0            0   
2             0        0          0      0        0            0   
3             0        0          0      0        0            0   
4             0        0          0      0        0            0   

   United Arab Emirates  Argentina  South Africa  Denmark  Croatia  Spain  \
0                     0          0             0        0        0      0   
1                     0          0             0        0        0      0   
2                     0          0             0        0        0      0   
3                     0          0             0        0        0      0   
4                     0          0             0        0        0      0   

   Paraguay  Germany  Serbia  Greece  Cambodia  India  New Zealand  Norway  \
0         0        0       0       0         0      0            0       0   
1         0        0       0       0         0      0            0       0   
2         0        0       0       0         0      0            0       0   
3         0        0       0       0         0      0            0       0   
4         0        0       0       0         0      0            0       0   

   Kenya  France  Brazil  Ghana  Belarus  Belgium  China  Italy  Poland  \
0      0       0       1      0        0        0      0      0       0   
1      0       0       0      0        0        0      0      0       0   
2      0       0       0      0        0        0      0      0       0   
3      0       0       0      0        0        0      0      0       0   
4      0       0       0      0        0        0      0      0       0   

   Switzerland  Mauritius  Georgia  Namibia  Japan  Zimbabwe  Cyprus  Jamaica  \
0            0          0        0        0      0         0       0        0   
1            0          0        0        0      0         0       0        0   
2            0          0        0        0      0         0       0        0   
3            0          0        0        0      0         0       0        0   
4            0          0        0        0      0         0       0        0   

   United Kingdom  Chile  Venezuela  Portugal  Mexico  Vietnam  Puerto Rico  \
0               0      0          0         0       0        0            0   
1               0      0          0         0       1        0            0   
2               0      0          0         0       0        0            0   
3               0      0          0         0       0        0            0   
4               0      0          0         0       0        0            0   

   Slovenia  Thailand  Pakistan  Iran  Senegal  United States  Singapore  \
0         0         0         0     0        0              0          0   
1         0         0         0     0        0              0          0   
2         0         0         0     0        0              0          1   
3         0         0         0     0        0              1          0   
4         0         0         0     0        0              1          0   

   nodata  Taiwan  Malaysia  Australia  Czech Republic  West Germany  Canada  \
0       0       0         0          0               0             0       0   
1       0       0         0          0               0             0       0   
2       0       0         0          0               0             0       0   
3       0       0         0          0               0             0       0   
4       0       0         0          0               0             0       0   

   Bangladesh  Lebanon  Uruguay  Hungary  Indonesia  Jordan  Soviet Union  \
0           0        0        0        0          0       0             0   
1           0        0        0        0          0       0             0   
2           0        0        0        0          0       0             0   
3  

In [14]:
# A.3. categorical: type, rating

#  type: Movie = 0 / TV Show = 1 (nominal)
dfv1['type'] = dfv1['type'].apply(lambda x: 0 if x=='Movie' else 1)

# rating: more audlt, get higher number (ordinary)
dfv1['rating'] = dfv1['rating'].apply(lambda x: 0 if x=='UR' or x=='nodata' or x=='NR'
                                      else 1 if x=='TV-Y' else 2 if x=='TV-Y7'
                                     else 3 if x=='TV-Y7-FV' else 4 if x=='G' or x=='TV-G'
                                     else 5 if x=='PG' or x=='TV-PG' else 6 if x=='TV-14' or x=='PG-13'
                                     else 7 if x=='R' else 8 if x=='TV-MA' or x=='NC-17' else 9)
        

In [15]:
# B. get cosine similarity 
# drop unnecessary column
dfv2 =dfv1.drop(columns=['cast','country','duration','listed_in','description','genre'],axis=1)

# B.1 TF-IDF(listed_in) & one-hot(country) & categorical(type,rating) (without cast)
# B.2 TF-IDF(description) & one-hot(country) & categorical
# B.3 one-hot encoding & categorical

# listed_in = tfidfv_g_df / description = tfidfv_d_df
# one-hot(country) = tf_ct / one-hot(cast) = tf_c
# categorical = dfv1['type'] , dfv1['rating'] 

In [16]:
# B.1 TF-IDF(listed_in) & one-hot(country) & categorical (without cast)
result_B1 = pd.concat([dfv2, tfidfv_g_df, tf_ct], join='outer', axis=1)
display(result_B1.head(5))

type  title  rating    action  adventure  anime  british  children  \
0     1     3%       8  0.000000   0.000000    0.0      0.0       0.0   
1     0   7:19       8  0.000000   0.000000    0.0      0.0       0.0   
2     0  23:59       7  0.000000   0.000000    0.0      0.0       0.0   
3     0      9       6  0.341928   0.341928    0.0      0.0       0.0   
4     0     21       6  0.000000   0.000000    0.0      0.0       0.0   

   classic  comedies  comedy  crime  cult  documentaries  docuseries  \
0      0.0       0.0     0.0    0.0   0.0            0.0         0.0   
1      0.0       0.0     0.0    0.0   0.0            0.0         0.0   
2      0.0       0.0     0.0    0.0   0.0            0.0         0.0   
3      0.0       0.0     0.0    0.0   0.0            0.0         0.0   
4      0.0       0.0     0.0    0.0   0.0            0.0         0.0   

     dramas  faith  family   fantasy  features        fi    horror  \
0  0.243763    0.0     0.0  0.515932       0.0  0.515932  0.000000   
1  0.753545    0.0     0.0  0.000000       0.0  0.000000  0.000000   
2  0.000000    0.0     0.0  0.000000       0.0  0.000000  0.915747   
3  0.000000    0.0     0.0  0.458116       0.0  0.458116  0.000000   
4  1.000000    0.0     0.0  0.000000       0.0  0.000000  0.000000   

   independent  international  kids  korean  language  lgbtq  music  musicals  \
0     0.000000       0.212660   0.0     0.0       0.0    0.0    0.0       0.0   
1     0.000000       0.657397   0.0     0.0       0.0    0.0    0.0       0.0   
2     0.000000       0.401756   0.0     0.0       0.0    0.0    0.0       0.0   
3     0.369539       0.000000   0.0     0.0       0.0    0.0    0.0       0.0   
4     0.000000       0.000000   0.0     0.0       0.0    0.0    0.0       0.0   

   mysteries  nature  reality  romantic       sci  science  series     shows  \
0        0.0     0.0      0.0       0.0  0.515932      0.0     0.0  0.311123   
1        0.0     0.0      0.0       0.0  0.000000      0.0     0.0  0.000000   
2        0.0     0.0      0.0       0.0  0.000000      0.0     0.0  0.000000   
3        0.0     0.0      0.0       0.0  0.458116      0.0     0.0  0.000000   
4        0.0     0.0      0.0       0.0  0.000000      0.0     0.0  0.000000   

   spanish  spirituality  sports  stand  talk  teen  thrillers   up  \
0      0.0           0.0     0.0    0.0   0.0   0.0        0.0  0.0   
1      0.0           0.0     0.0    0.0   0.0   0.0        0.0  0.0   
2      0.0           0.0     0.0    0.0   0.0   0.0        0.0  0.0   
3      0.0           0.0     0.0    0.0   0.0   0.0        0.0  0.0   
4      0.0           0.0     0.0    0.0   0.0   0.0        0.0  0.0   

   Saudi Arabia  Somalia  Hong Kong  Egypt  Austria  Netherlands  \
0             0        0          0      0        0            0   
1             0        0          0      0        0            0   
2             0        0          0      0        0            0   
3             0        0          0      0        0            0   
4             0        0          0      0        0            0   

   United Arab Emirates  Argentina  South Africa  Denmark  Croatia  Spain  \
0                     0          0             0        0        0      0   
1                     0          0             0        0        0      0   
2                     0          0             0        0        0      0   
3                     0          0             0        0        0      0   
4                     0          0             0        0        0      0   

   Paraguay  Germany  Serbia  Greece  Cambodia  India  New Zealand  Norway  \
0         0        0       0       0         0      0            0       0   
1         0        0       0       0         0      0            0       0   
2         0        0       0       0         0      0            0       0   
3         0        0       0       0         0      0            0       0   
4         0        0       0       0         0      0

In [22]:
def recommend_genre(title):
    if title in list(result_B1['title']):
        mov=result_B1[result_B1['title']==title]
        dfn= result_B1[result_B1['title']!=title]
        new_df = dfn.copy()
        new_df.loc[1, 'cos'] = 'ok' #to avoid pandas copywarning
        n0 = new_df.shape[0]
        n1 = new_df.shape[1]
        t = np.array(mov.iloc[0,np.r_[0,2:n1-1]])
        for i in range(n0):
            c = cos_sim(np.array(new_df.iloc[i,np.r_[0,2:n1-1]]),t)
            new_df.loc[i+1, 'cos'] = c

        sort = new_df.sort_values('cos',ascending=False)
        title_5 = sort.head(5)
        return title_5[['title','cos']]
    else: return ('cannont find title you want')

# for example = print 5 movies similar to movie called '3%'
recommend_genre('3%')


title       cos
4611            Omniscient         1
4502      Nobody's Looking  0.990729
4233  Most Beautiful Thing  0.990635
989             Blood Pact  0.990344
5635              Sintonia  0.990344

In [41]:
# B.2 one-hot TF(description, country) & categorical(type, rating) (without cast)
# because columns are duplicated with word of description, rename column of dfv2
dfv3=dfv2.rename(columns={'title': 'mov_title','type':'tvmovtype','rating': 'aged_type'})
result_B2 = pd.concat([dfv3,tf_d, tf_ct], join='inner', axis=1)
display(result_B2.head(5))

tvmovtype mov_title  aged_type  debut  junkyard  Yijuan  quarry  \
0          1        3%          8      0         0       0       0   
1          0      7:19          8      0         0       0       0   
2          0     23:59          7      0         0       0       0   
3          0         9          6      0         0       0       0   
4          0        21          6      0         0       0       0   

   propaganda  boomer  clown  break  conglomerate  autobiography  prank  \
0           0       0      0      0             0              0      0   
1           0       0      0      0             0              0      0   
2           0       0      0      0             0              0      0   
3           0       0      0      0             0              0      0   
4           0       0      0      0             0              0      0   

   casino  vistas  curmudgeon  cabdriver  programmer  orcas  go-to-guy  \
0       0       0           0          0           0      0          0   
1       0       0           0          0           0      0          0   
2       0       0           0          0           0      0          0   
3       0       0           0          0           0      0          0   
4       1       0           0          0           0      0          0   

   stride  cage  vulnerability  gem  gladiator  Zixin  hamster  lock  rec  \
0       0     0              0    0          0      0        0     0    0   
1       0     0              0    0          0      0        0     0    0   
2       0     0              0    0          0      0        0     0    1   
3       0     0              0    0          0      0        0     0    0   
4       0     0              0    0          0      0        0     0    0   

   skin  noblewoman  artist  threat  democracy  has-been  midnight  staff  \
0     0           0       0       0          0         0         0      0   
1     0           0       0       0          0         0         0      0   
2     0           0       0       0          0         0         0      0   
3     0           0       0       0          0         0         0      0   
4     0           0       0       0          0         0         0      0   

   cartoonist  packed  tech  activist  impression  indecisiveness  fairness  \
0           0       0     0         0           0               0         0   
1           0       0     0         0           0               0         0   
2           0       0     0         0           0               0         0   
3           0       0     0         0           0               0         0   
4           0       0     0         0           0               0         0   

   winner  gangland  tip  missing  harm  Manipulation  shaken  bungalow  \
0       0         0    0        0     0             0       0         0   
1       0         0    0        0     0             0       0         0   
2       0         0    0        0     0             0       0         0   
3       0         0    0        0     0             0       0         0   
4       0         0    0        0     0             0       0         0   

   supervisor  absence  outrage  await  kitchen  shipment  pigeon  \
0           0        0        0      0        0         0       0   
1           0        0        0      0        0         0       0   
2           0        0        0      0        0         0       0   
3           0        0        0      0        0         0       0   
4           0        0        0      0        0         0       0   

   bride-to-be  protection  deceit  Life  reishi  desert  Nate  cleansing  \
0            0           0       0     0       0       0     0          0   
1            0           0       0     0       0       0     0          0   
2            0           0       0     0       0       0     0          0   
3            0           0       0     0       0       0     0          0   
4            0           0       0

In [44]:
# it would take time because of over 5000 words so quit
def recommend_description(title):
    if title in list(result_B2['mov_title']):
        mov=result_B2[result_B2['mov_title']==title]
        dfn= result_B2[result_B2['mov_title']!=title]
        new_df = dfn.copy()
        new_df.loc[1, 'cos'] = 'ok' # to avoid pandas copywarning
        n0 = new_df.shape[0]
        n1 = new_df.shape[1]
        t = np.array(mov.iloc[0,np.r_[0,2:n1-1]])
        for i in range(n0):
            c = cos_sim(np.array(new_df.iloc[i,np.r_[0,2:n1-1]]),t)
            new_df.loc[i+1, 'cos'] = c

        sort = new_df.sort_values('cos',ascending=False)
        title_5 = sort.iloc[:5,:]
        return title_5[['mov_title','cos']]
    else: return ('cannont find title you want')
# for example = print 5 movies similar to movie called '3%'
recommend_description('3%')

mov_title       cos
3014                     Inside The Freemasons  0.913464
5129                   Record of Grancrest War  0.912078
2256  Francesco De Carlo: Cose di Questo Mondo  0.911917
5741                                 Spartacus  0.909908
2403                            Ghost Whispers  0.908932

In [32]:
# B.3 one-hot encoding & categorical
# one-hot encoding = cast, country
# categorical=type, rating
result_B3 = pd.concat([dfv2, tf_c, tf_ct], join='outer', axis=1)
display(result_B3.head(5))

type  title  rating  Fiona Dourif  Neal Brennan  Robert Więckiewicz  \
0     1     3%       8             0             0                   0   
1     0   7:19       8             0             0                   0   
2     0  23:59       7             0             0                   0   
3     0      9       6             0             0                   0   
4     0     21       6             0             0                   0   

   Gerard Butler  Subbu Talabi  Amber Kuo  Judy Davis  Michael Jordan  \
0              0             0          0           0               0   
1              0             0          0           0               0   
2              0             0          0           0               0   
3              0             0          0           0               0   
4              0             0          0           0               0   

   Saad El Soghayar  Jacqueline Kim  Emre Karayel  Riley Wang  \
0                 0               0             0           0   
1                 0               0             0           0   
2                 0               0             0           0   
3                 0               0             0           0   
4                 0               0             0           0   

   David Hasselhoff  Felicia Day  Inthira Charoenpura  Riddhi Sen  \
0                 0            0                    0           0   
1                 0            0                    0           0   
2                 0            0                    0           0   
3                 0            0                    0           0   
4                 0            0                    0           0   

   Randy Wayne  Sidse Babett Knudsen  Maciej Musiałowski  Wu Kang-jen  \
0            0                     0                   0            0   
1            0                     0                   0            0   
2            0                     0                   0            0   
3            0                     0                   0            0   
4            0                     0                   0            0   

   Rahul Bairagi  Olasupo Shasore  Yvan Attal  Nayantara  Siddharth Koirala  \
0              0                0           0          0                  0   
1              0                0           0          0                  0   
2              0                0           0          0                  0   
3              0                0           0          0                  0   
4              0                0           0          0                  0   

   Nicholas Braun  Johnathon Schaech  Fawad Khan  Parvathy Ratheesh  \
0               0                  0           0                  0   
1               0                  0           0                  0   
2               0                  0           0                  0   
3               0                  0           0                  0   
4               0                  0           0                  0   

   Joel Gretsch  Jim Henson  Travis Scott  Eugenio Derbez  Stefanie Scott  \
0             0           0             0               0               0   
1             0           0             0               0               0   
2             0           0             0               0               0   
3             0           0             0               0               0   
4             0           0             0               0               0   

   Leslie Jones  Carla Gugino  Ralph Macchio  Garth Brooks  Trevante Rhodes  \
0             0             0              0             0                0   
1             0             0              0             0                0   
2             0             0              0             0                0   
3             0             0              0             0                0   
4             0             0              0             0                0   

   Nour Al Ghandour  David Samplin

In [33]:
# it would take time 
def recommend_cast_country(title):
    if title in list(result_B3['title']):
        mov=result_B3[result_B3['title']==title]
        dfn= result_B3[result_B3['title']!=title]
        new_df = dfn.copy()
        new_df.loc[1, 'cos'] = 'ok' # to avoid pandas copywarning
        n0 = new_df.shape[0]
        n1 = new_df.shape[1]
        t = np.array(mov.iloc[0,np.r_[0,2:n1-1]])
        for i in range(n0):
            c = cos_sim(np.array(new_df.iloc[i,np.r_[0,2:n1-1]]),t)
            new_df.loc[i+1, 'cos'] = c

        sort = new_df.sort_values('cos',ascending=False)
        title_5 = sort.iloc[:5,:]
        return title_5[['title','cos']]
    else: return ('cannont find title you want')
# for example = print 5 movies similar to movie called '3%'
recommend_cast_country('3%')

title       cos
4611              Omniscient  0.985294
1115             Brotherhood  0.985294
3416            Kissing Game  0.985294
2486  Good Morning, Verônica  0.985294
989               Blood Pact  0.978645

In [ ]:
# # Option
# # tf-idf for manually for description 
# voc_d=[]
# for text in arr_d:
#     term = nltk.word_tokenize(text)
#     qu = nltk.pos_tag(term)
#     for e in qu:
#         if e[1]=='NN':
#             voc_d.append(e[0])
            
# voc_ds=list(set(voc_d))
# N = len(arr_d) 

# def idf(t):
#     df = 0
#     for doc in arr_d:
#         df += t in doc
#     return log(N/(df + 1))

# tf_d = []
# for i in range(N): 
#     tf_d.append([])
#     d = arr_d[i]
#     for j in range(len(voc_ds)):
#         t = voc_ds[j]        
#         tf_d [-1].append(tf(t, d))
# tf_Df= pd.DataFrame(tf_d, columns = voc_ds)

# idf_d = []
# for j in range(len(voc_ds)):
#     t = voc_ds[j]
#     idf_d.append(idf(t))

# idf_Df = pd.DataFrame(idf_d , index = voc_ds, columns = ["IDF"])

# #td_idf
# for i in range(tf_Df.shape[0]):
#     idf = idf_Df.iloc[0,:].values[0]
#     tf_Df.iloc[:,i]=tf_Df.iloc[:,i]*idf